In [1]:
import random
import numpy as np
import pandas as pd
import scipy.stats as sps
import plotly.graph_objs as go

## 1. Критерий Стьюдента
Реализовать t-критерий Стьюдента для 2 независимых выборок при условии неизвестной дисперсии. Необходимо считать значение статистики и p_value для разных видов гипотез (двусторонняя, односторонние), а также результат (отвергается нулевая гипотеза или нет). Сравнить результаты с реализацией в scipy.stats.ttest_ind. 

### 1.1 Дисперсии неизвестны и равны, двусторонний критерий 

Реализуем 2 независимые выборки из нормального распределения со средними m1, m2, и неизвестными дисперсиями. Предположим, что дисперсии равны (так как нам не дано обратное) 

In [2]:
m1 = random.randint(1, 10)
m2 = m1
s1 = random.randint(1, 10)
s2 = s1

n1, n2 = 100, 1000
x1 = sps.norm.rvs(loc=m1, scale=s1, size=n1)
mean_1 = x1.mean()
std_1 = x1.std(ddof=1)

x2 = sps.norm.rvs(loc=m2, scale=s2, size=n2)
mean_2 = x2.mean()
std_2 = x2.std(ddof=1)

sts, p_val = sps.stats.ttest_ind(x1, x2, equal_var=True, alternative='two-sided')

C:\Users\tatiana\AppData\Local\Temp\ipykernel_9708\1338502721.py:15: DeprecationWarning: Please use `ttest_ind` from the `scipy.stats` namespace, the `scipy.stats.stats` namespace is deprecated.
  sts, p_val = sps.stats.ttest_ind(x1, x2, equal_var=True, alternative='two-sided')


In [3]:
mean_1, mean_2

(8.114428730520197, 7.323321477637599)

In [4]:
std_1, std_2

(8.58072585196251, 8.817485285544306)

В случае неизвестных, но равных дисперсий для проверки гипотезы равенства средних используется t статистика

С помощью критерия Стьюдента будем проверять гипотезу о равенстве средних значений выборок, считая дисперсии равными на 95% уровне доверия против двусторонних альтернатив.

    Н0: m1 = m2 средние двух независимых выборок равны
    Н1: m1 != m2 средние двух независимых выборок не равны
    
Критическая область двусторонняя, по таблице t - распределения находим нужное критическое значение при заданном alpha = 0.05, число степеней свободы n = n1 + n2 - 2 = 1098, tcr = +-1,96, критическая область имеет вид (-inf, -1.96, 1.96, +inf). 

Вычислим объединенную оценку дисперсии:

In [6]:
sp = ((n1 - 1) * std_1 ** 2 + (n2 - 1) * std_2 ** 2) / (n1 + n2 - 2)

Посчитаем значение статистики критерия:

In [7]:
t = (mean_1 - mean_2) / np.sqrt((sp ** 2)/n1 + (sp ** 2)/n2)
t

0.0974830552877789

Вывод: полученное значение t лежит вне интервала (-inf, -1.96, 1.96, +inf), нет оснований отвергнуть Н0 гипотезу на уровне значимости alpha

Проверка: 

In [9]:
p_val < 0.05

False

### 1.2 Дисперсии неизвестны и равны, односторонний критерий

In [10]:
m1 = random.randint(1, 10)
m2 = m1
s1 = random.randint(1, 10)
s2 = s1

n1, n2 = 100, 1000
x1 = sps.norm.rvs(loc=m1, scale=s1, size=n1)
mean_1 = x1.mean()
std_1 = x1.std(ddof=1)

x2 = sps.norm.rvs(loc=m2, scale=s2, size=n2)
mean_2 = x2.mean()
std_2 = x2.std(ddof=1)

sts, p_val = sps.stats.ttest_ind(x1, x2, equal_var=True, alternative='greater')
print('T statistic with pystats:', sts, 'p value', p_val)

T statistic with pystats: 0.004516038455453443 p value 0.4981987776107334


C:\Users\tatiana\AppData\Local\Temp\ipykernel_9708\2329458175.py:15: DeprecationWarning: Please use `ttest_ind` from the `scipy.stats` namespace, the `scipy.stats.stats` namespace is deprecated.
  sts, p_val = sps.stats.ttest_ind(x1, x2, equal_var=True, alternative='greater')


In [11]:
mean_1, mean_2

(6.8883448065625466, 6.886531793868142)

In [12]:
std_1, std_2

(3.4738232053950147, 3.8610891383324715)

Сформулируем гипотезы: 

    Н0: m1 = m2
    H1: m1 > m2
    
Критическая область односторонняя, по таблице t - распределения находим нужное критическое значение при заданном alpha = 0.05, число степеней свободы n = n1 + n2 - 2 = 1098, tcr = 1,96,  критическая область будет правосторонней и выглядеть так: (1.96, inf)

In [13]:
sp = ((n1 - 1) * std_1 ** 2 + (n2 - 1) * std_2 ** 2) / (n1 + n2 - 2)
sp

14.651893117838423

In [14]:
t = (mean_1 - mean_2) / np.sqrt((sp ** 2)/n1 + (sp ** 2)/n2)
t

0.001179806434595035

t статистика лежит вне критической области, значит, нет оснований отвергнуть нулевую гипотезу на уровне значимости альфа

In [15]:
p_val < 0.05

False

Так как p_value > alpha, мы не можем отвергнуть нулевую гипотезу теста на уровне значимости alpha

## 2. Bootstrap
Реализовать bootstrap для оценки (через доверительные интервалы) медианных и средних значений распределений. Рассчитать для распределений: нормальное, экспоненциальное, смесь нормальных

In [16]:
def get_bootstrap_sample_indices(sample_size: int, n_samples: int) -> np.ndarray:
    return np.random.randint(0, sample_size, (n_samples, sample_size))

def get_bootstrap_samples(X: np.ndarray, n_samples: int) -> np.ndarray:
    return X[get_bootstrap_sample_indices(len(X), n_samples)]

In [17]:
size = 100
x_norm1 = sps.expon.rvs(loc=4, scale=16, size=size)
x_exp = sps.expon.rvs(loc=10, scale=10, size=size)
x_norm2 = sps.expon.rvs(loc=3, scale=11, size=size)
x_sum = np.append(x_norm1,x_norm2)

X1_bootstrap = get_bootstrap_samples(x_norm1, n_samples=10_000)
X2_bootstrap = get_bootstrap_samples(x_exp, n_samples=10_000)
X3_boostrap = get_bootstrap_samples(x_sum, n_samples=10_000)

X1_mean = X1_bootstrap.mean(axis=1)
X1_median = np.median(X1_bootstrap, axis=1)
X2_mean = X2_bootstrap.mean(axis=1)
X2_median = np.median(X2_bootstrap, axis=1)
X3_mean = X3_boostrap.mean(axis=1)
X3_median = np.median(X3_boostrap, axis=1)

In [18]:
go.Figure([go.Histogram(x=X1_mean)])

In [19]:
alpha = 0.05
CI_mean1 = np.percentile(X1_mean, (alpha * 100, (1-alpha) * 100))
CI_median1 = np.percentile(X1_median, (alpha * 100, (1-alpha) * 100))

CI_mean2 = np.percentile(X2_mean, (alpha * 100, (1-alpha) * 100))
CI_median2 = np.percentile(X2_median, (alpha * 100, (1-alpha) * 100))

CI_mean3 = np.percentile(X3_mean, (alpha * 100, (1-alpha) * 100))
CI_median3 = np.percentile(X3_median, (alpha * 100, (1-alpha) * 100))

In [20]:
print('Доверительный интервал для среднего выборки x_norm1', CI_mean1)
print('Доверительный интервал для медианы выборки x_norm1', CI_median1)
print()
print('Доверительный интервал для среднего выборки x_exp', CI_mean2)
print('Доверительный интервал для медианы выборки x_exp', CI_median2)
print()
print('Доверительный интервал для среднего выборки x_sum', CI_mean3)
print('Доверительный интервал для медианы выборки x_sum', CI_median3)

Доверительный интервал для среднего выборки x_norm1 [15.68826916 20.1848    ]
Доверительный интервал для медианы выборки x_norm1 [12.14101373 16.37307817]

Доверительный интервал для среднего выборки x_exp [17.76997765 21.14899099]
Доверительный интервал для медианы выборки x_exp [15.51239145 18.35093792]

Доверительный интервал для среднего выборки x_sum [14.59647141 17.55803291]
Доверительный интервал для медианы выборки x_sum [11.41468235 13.42668337]


## 3. Мощность
Рассчитать мощность критерия для t-критерия и критерия Манна-Уитни для разных распределений и разном эффекте. Отдельно изучить случай, когда средние равны, а дисперсии сильно отличаются.

t-test

In [21]:
size = 30
n_exp = 100
alpha = 0.05

p1_values = []
p2_values = []
for i in range(n_exp):
    # случай, когда дисперсии равны
    x1_norm = sps.norm.rvs(loc=10, scale=3, size=size)
    x2_norm = sps.norm.rvs(loc=10 + 3, scale=3, size=size) # хотим заметить маленький эффект
    
    x1_exp = sps.expon.rvs(loc=10, scale=3, size=size)
    x2_exp = sps.expon.rvs(loc=10 + 3, scale=3, size=size) # эффект побольше
    
    p1_value = sps.ttest_ind(x1_norm, x2_norm).pvalue
    p2_value = sps.ttest_ind(x1_exp, x2_exp).pvalue
    
    p1_values.append(p1_value)
    p2_values.append(p2_value)
    
p1_values = np.array(p1_values)
p2_values = np.array(p2_values)

In [22]:
p1_values[p1_values < alpha].shape[0] / p1_values.shape[0] * 100

100.0

In [23]:
p2_values[p2_values < alpha].shape[0] / p2_values.shape[0] * 100

97.0

Средние равны, а дисперсии сильно отличаются

In [24]:
size = 200
n_exp = 100
alpha = 0.05

p1_values = []
p2_values = []
for i in range(n_exp):
    x1_norm = sps.norm.rvs(loc=10, scale=3, size=size)
    x2_norm = sps.norm.rvs(loc=10 + 3, scale=13, size=size) # хотим заметить маленький эффект
    
    x1_exp = sps.expon.rvs(loc=10, scale=3, size=size)
    x2_exp = sps.expon.rvs(loc=10 + 3, scale=13, size=size) # эффект побольше
    
    p1_value = sps.ttest_ind(x1_norm, x2_norm).pvalue
    p2_value = sps.ttest_ind(x1_exp, x2_exp).pvalue
    
    p1_values.append(p1_value)
    p2_values.append(p2_value)
    
p1_values = np.array(p1_values)
p2_values = np.array(p2_values)

Оценка мощности

In [25]:
p1_values[p1_values < alpha].shape[0] / p1_values.shape[0] * 100

91.0

In [26]:
p2_values[p2_values < alpha].shape[0] / p2_values.shape[0] * 100

100.0

Критерий Манна-Уитни

In [27]:
size = 40
n_exp = 100
alpha = 0.05

p1_values = []
p2_values = []
for i in range(n_exp):
    # случай, когда дисперсии равны
    x1_norm = sps.norm.rvs(loc=10, scale=3, size=size)
    x2_norm = sps.norm.rvs(loc=10 + 3, scale=3, size=size) # хотим заметить маленький эффект
    
    x1_exp = sps.expon.rvs(loc=10, scale=3, size=size)
    x2_exp = sps.expon.rvs(loc=10 + 3, scale=3, size=size) # эффект побольше
    
    p1_value = sps.mannwhitneyu(x1_norm, x2_norm).pvalue
    p2_value = sps.mannwhitneyu(x1_exp, x2_exp).pvalue
    
    p1_values.append(p1_value)
    p2_values.append(p2_value)
    
p1_values = np.array(p1_values)
p2_values = np.array(p2_values)

In [28]:
p1_values[p1_values < alpha].shape[0] / p1_values.shape[0] * 100

99.0

In [29]:
p2_values[p2_values < alpha].shape[0] / p2_values.shape[0] * 100

100.0

Средние равны, а дисперсии сильно отличаются

In [30]:
size = 200
n_exp = 100
alpha = 0.05

p1_values = []
p2_values = []
for i in range(n_exp):
    x1_norm = sps.norm.rvs(loc=10, scale=3, size=size)
    x2_norm = sps.norm.rvs(loc=10 + 3, scale=13, size=size) # хотим заметить маленький эффект
    
    x1_exp = sps.expon.rvs(loc=10, scale=3, size=size)
    x2_exp = sps.expon.rvs(loc=10 + 3, scale=13, size=size) # эффект побольше
    
    p1_value = sps.mannwhitneyu(x1_norm, x2_norm).pvalue
    p2_value = sps.mannwhitneyu(x1_exp, x2_exp).pvalue
    
    p1_values.append(p1_value)
    p2_values.append(p2_value)
    
p1_values = np.array(p1_values)
p2_values = np.array(p2_values)

In [31]:
p1_values[p1_values < alpha].shape[0] / p1_values.shape[0] * 100

85.0

In [32]:
p2_values[p2_values < alpha].shape[0] / p2_values.shape[0] * 100

100.0

В случае, когда средние равны, а дисперсии сильно отличаются, для достижени той же мощности критерия, что и в предыдущем примере, нужно значительно больше данных


## 4. Корректность
Оценить корректность t-критерия и критерия Манна-Уитни на разных распределениях

In [33]:
alpha = 0.05

size = 100
n_exp = 10000

p1_values = []
p2_values = []
p3_values = []
for i in range(n_exp):
    x1_norm = sps.norm.rvs(loc=10, scale=2, size=size)
    x2_norm = sps.norm.rvs(loc=10, scale=2, size=size)
    p1_value = sps.ttest_ind(x1_norm, x2_norm, equal_var=False).pvalue

    x1_exp = sps.expon.rvs(scale=1/2, size=size)
    x2_exp = sps.expon.rvs(scale=1/2, size=size)
    p2_value = sps.ttest_ind(x1_exp, x2_exp, equal_var=False).pvalue
    
    x1_sum = np.append(
        sps.norm.rvs(loc=3, scale=1, size=size),
        sps.norm.rvs(loc=2.5, scale=0.1, size=size),)
    x2_sum = np.append(
        sps.norm.rvs(loc=3, scale=1, size=size),
        sps.norm.rvs(loc=2.5, scale=0.1, size=size),)
    p3_value = sps.ttest_ind(x1_sum, x2_sum).pvalue
    
    p1_values.append(p1_value)
    p2_values.append(p2_value)
    p3_values.append(p3_value)

p1_values = np.array(p1_values)
p2_values = np.array(p2_values)
p3_values = np.array(p3_values)

Нормальные распределения

In [34]:
fig = go.Figure([go.Histogram(x=x1_norm, opacity=0.8),
                 go.Histogram(x=x2_norm, opacity=0.8)])
fig.update_layout(barmode="overlay")

In [35]:
p1_values[p1_values < alpha].shape[0] / p1_values.shape[0]

0.0513

In [36]:
probs = []
x = [0.01 * i for i in range(101)]
for i in range(101):
    alpha_step = 0.01 * i
    probs.append(p1_values[p1_values < alpha_step].shape[0] / p1_values.shape[0])

fig = go.Figure([go.Scatter(x=x, y=probs, mode="markers", name="p_value"),
                 go.Scatter(x=x, y=x, mode="lines", name="uniform")])
fig.update_layout(height=600, width=600, title="Q-Q plot")

In [37]:
fig = go.Figure([go.Histogram(x=p1_values, xbins={"start":0, "end":1, "size": 0.1})])
fig

Экспоненциальное распределение.

In [38]:
fig = go.Figure([go.Histogram(x=x1_exp, opacity=0.8),
                 go.Histogram(x=x2_exp, opacity=0.8)])
fig.update_layout(barmode="overlay")

In [39]:
p2_values[p2_values < alpha].shape[0] / p2_values.shape[0]

0.048

In [40]:
probs = []
x = [0.01 * i for i in range(101)]
for i in range(101):
    alpha_step = 0.01 * i
    probs.append(p2_values[p2_values < alpha_step].shape[0] / p2_values.shape[0])

fig = go.Figure([go.Scatter(x=x, y=probs, mode="markers", name="p_value"),
                 go.Scatter(x=x, y=x, mode="lines", name="uniform")])
fig.update_layout(height=600, width=600, title="Q-Q plot")

In [41]:
fig = go.Figure([go.Histogram(x=p2_values, xbins={"start":0, "end":1, "size": 0.1})])
fig

Смесь распределений

In [42]:
fig = go.Figure([go.Histogram(x=x1_sum, opacity=0.8),
                 go.Histogram(x=x2_sum, opacity=0.8)])
fig.update_layout(barmode="overlay")

In [43]:
p3_values[p3_values < alpha].shape[0] / p3_values.shape[0]

0.0356

In [44]:
probs = []
x = [0.01 * i for i in range(101)]
for i in range(101):
    alpha_step = 0.01 * i
    probs.append(p3_values[p3_values < alpha_step].shape[0] / p3_values.shape[0])

fig = go.Figure([go.Scatter(x=x, y=probs, mode="markers", name="p_value"),
                 go.Scatter(x=x, y=x, mode="lines", name="uniform")])
fig.update_layout(height=600, width=600, title="Q-Q plot")

In [45]:
fig = go.Figure([go.Histogram(x=p3_values, xbins={"start":0, "end":1, "size": 0.1})])
fig

Критерий Манна-Уитни

In [46]:
alpha = 0.05

size = 100
n_exp = 10000

p1_values = []
p2_values = []
p3_values = []
for i in range(n_exp):
    x1_norm = sps.norm.rvs(loc=10, scale=2, size=size)
    x2_norm = sps.norm.rvs(loc=10, scale=2, size=size)
    p1_value = sps.mannwhitneyu(x1_norm, x2_norm).pvalue
    
    x1_exp = sps.expon.rvs(scale=1/2, size=size)
    x2_exp = sps.expon.rvs(scale=1/2, size=size)
    p2_value = sps.mannwhitneyu(x1_exp, x2_exp).pvalue
    
    x1_sum = np.append(
        sps.norm.rvs(loc=3, scale=1, size=size),
        sps.norm.rvs(loc=2.5, scale=0.1, size=size),)
    x2_sum = np.append(
        sps.norm.rvs(loc=3, scale=1, size=size),
        sps.norm.rvs(loc=2.5, scale=0.1, size=size),)
    p3_value = sps.mannwhitneyu(x1_sum, x2_sum).pvalue
    
    p1_values.append(p1_value)
    p2_values.append(p2_value)
    p3_values.append(p3_value)

p1_values = np.array(p1_values)
p2_values = np.array(p2_values)
p3_values = np.array(p3_values)

In [47]:
fig = go.Figure([go.Histogram(x=x1_sum, opacity=0.8),
                 go.Histogram(x=x2_sum, opacity=0.8)])
fig.update_layout(barmode="overlay")

In [48]:
p1_values[p1_values < alpha].shape[0] / p1_values.shape[0]

0.0501

In [49]:
probs = []
x = [0.01 * i for i in range(101)]
for i in range(101):
    alpha_step = 0.01 * i
    probs.append(p1_values[p1_values < alpha_step].shape[0] / p1_values.shape[0])

fig = go.Figure([go.Scatter(x=x, y=probs, mode="markers", name="p_value"),
                 go.Scatter(x=x, y=x, mode="lines", name="uniform")])
fig.update_layout(height=600, width=600, title="Q-Q plot")

In [50]:
fig = go.Figure([go.Histogram(x=p1_values, xbins={"start":0, "end":1, "size": 0.1})])
fig

In [51]:
fig = go.Figure([go.Histogram(x=x1_exp, opacity=0.8),
                 go.Histogram(x=x2_exp, opacity=0.8)])
fig.update_layout(barmode="overlay")

In [52]:
p2_values[p2_values < alpha].shape[0] / p2_values.shape[0]

0.0527

In [53]:
probs = []
x = [0.01 * i for i in range(101)]
for i in range(101):
    alpha_step = 0.01 * i
    probs.append(p2_values[p2_values < alpha_step].shape[0] / p2_values.shape[0])

fig = go.Figure([go.Scatter(x=x, y=probs, mode="markers", name="p_value"),
                 go.Scatter(x=x, y=x, mode="lines", name="uniform")])
fig.update_layout(height=600, width=600, title="Q-Q plot")

In [54]:
fig = go.Figure([go.Histogram(x=p2_values, xbins={"start":0, "end":1, "size": 0.1})])
fig

In [55]:
fig = go.Figure([go.Histogram(x=x1_sum, opacity=0.8),
                 go.Histogram(x=x2_sum, opacity=0.8)])
fig.update_layout(barmode="overlay")

In [56]:
p3_values[p3_values < alpha].shape[0] / p3_values.shape[0]

0.0396

In [57]:
probs = []
x = [0.01 * i for i in range(101)]
for i in range(101):
    alpha_step = 0.01 * i
    probs.append(p3_values[p3_values < alpha_step].shape[0] / p3_values.shape[0])

fig = go.Figure([go.Scatter(x=x, y=probs, mode="markers", name="p_value"),
                 go.Scatter(x=x, y=x, mode="lines", name="uniform")])
fig.update_layout(height=600, width=600, title="Q-Q plot")

In [58]:
fig = go.Figure([go.Histogram(x=p3_values, xbins={"start":0, "end":1, "size": 0.1})])
fig